In [1]:
import pandas as pd
import numpy as np

In [2]:
data_train = pd.read_csv('./data_guane/datos_procesados_OHLC_5T_EURUSD-2018-01.csv',index_col=0,
                         parse_dates=True, infer_datetime_format=True)

In [3]:
print(data_train.shape)
data_train.head()

(6361, 5)


open     high      low      bid      ask
2018-01-02 00:00:00  1.20094  1.20094  1.20011  1.20015  1.20110
2018-01-02 00:05:00  1.20015  1.20062  1.20011  1.20047  1.20084
2018-01-02 00:10:00  1.20039  1.20098  1.20035  1.20082  1.20126
2018-01-02 00:15:00  1.20080  1.20097  1.20025  1.20035  1.20091
2018-01-02 00:20:00  1.20034  1.20057  1.20031  1.20049  1.20085

In [4]:
%run ../../code/EUtilities.py
EU = EUtilities()

In [5]:
window = 7
X, y_reg, bt = EU.build_dataset(data_train, window=window, bid_col='bid', binary_target=True, PNL=True)

In [6]:
X.head()

0        1        2        3        4        5  \
2018-01-02 00:30:00  1.20015  1.20047  1.20082  1.20035  1.20049  1.20047   
2018-01-02 00:35:00  1.20047  1.20082  1.20035  1.20049  1.20047  1.20079   
2018-01-02 00:40:00  1.20082  1.20035  1.20049  1.20047  1.20079  1.20135   
2018-01-02 00:45:00  1.20035  1.20049  1.20047  1.20079  1.20135  1.20143   
2018-01-02 00:50:00  1.20049  1.20047  1.20079  1.20135  1.20143  1.20149   

                           6    PNL_0    PNL_1  
2018-01-02 00:30:00  1.20079 -0.00076  0.00022  
2018-01-02 00:35:00  1.20135 -0.00023 -0.00012  
2018-01-02 00:40:00  1.20143 -0.00020 -0.00009  
2018-01-02 00:45:00  1.20149 -0.00007 -0.00030  
2018-01-02 00:50:00  1.20133 -0.00028 -0.00017

In [7]:
X['open'] = data_train.filter(X.index,axis=0).open
X['high'] = data_train.filter(X.index,axis=0).high
X['low'] = data_train.filter(X.index,axis=0).low

In [8]:
X.head()

0        1        2        3        4        5  \
2018-01-02 00:30:00  1.20015  1.20047  1.20082  1.20035  1.20049  1.20047   
2018-01-02 00:35:00  1.20047  1.20082  1.20035  1.20049  1.20047  1.20079   
2018-01-02 00:40:00  1.20082  1.20035  1.20049  1.20047  1.20079  1.20135   
2018-01-02 00:45:00  1.20035  1.20049  1.20047  1.20079  1.20135  1.20143   
2018-01-02 00:50:00  1.20049  1.20047  1.20079  1.20135  1.20143  1.20149   

                           6    PNL_0    PNL_1     open     high      low  
2018-01-02 00:30:00  1.20079 -0.00076  0.00022  1.20048  1.20093  1.20045  
2018-01-02 00:35:00  1.20135 -0.00023 -0.00012  1.20079  1.20163  1.20073  
2018-01-02 00:40:00  1.20143 -0.00020 -0.00009  1.20129  1.20145  1.20129  
2018-01-02 00:45:00  1.20149 -0.00007 -0.00030  1.20143  1.20150  1.20134  
2018-01-02 00:50:00  1.20133 -0.00028 -0.00017  1.20150  1.20150  1.20131

In [9]:
print('target 0: ', sum(bt==0))
print('target 1: ', sum(bt==1))
print('target 2: ', sum(bt==2))
print('target 3: ', sum(bt==3))

target 0:  2686
target 1:  2742
target 2:  400
target 3:  404


In [10]:
for i in EU.v_split(X,4,1,1):
    print('train: ',i[0][0],i[0][-1],'test: ', i[1][0],i[1][-1])

train:  0 1121 test:  1122 1122
train:  278 1122 test:  1123 1401
train:  562 1401 test:  1402 1684
train:  840 1684 test:  1685 1965
train:  1122 1965 test:  1966 2247
train:  1123 2247 test:  2248 2527
train:  1402 2527 test:  2528 2528
train:  1685 2528 test:  2529 2808
train:  1966 2808 test:  2809 3090
train:  2248 3090 test:  3091 3378
train:  2528 3378 test:  3379 3660
train:  2529 3660 test:  3661 3943
train:  2809 3943 test:  3944 3944
train:  3091 3944 test:  3945 4226
train:  3379 4226 test:  4227 4506
train:  3661 4506 test:  4507 4788
train:  3944 4788 test:  4789 5074
train:  3945 5074 test:  5075 5358
train:  4227 5358 test:  5359 5359
train:  4507 5359 test:  5360 5640
train:  4789 5640 test:  5641 5921
train:  5075 5921 test:  5922 6208
train:  5359 6208 test:  6209 6231


In [11]:
from keras.models import Sequential
from keras.utils import to_categorical
from sklearn.preprocessing import MinMaxScaler
from keras.layers import Dense, Dropout, Activation, LSTM, Embedding
from keras.optimizers import RMSprop, SGD

Using TensorFlow backend.


In [12]:
X_test_PNL_0 = X.PNL_0[833:1113]
X_test_PNL_1 = X.PNL_1[833:1113]

In [13]:
X_train = np.array(X[[col for col in X.columns if col!='PNL_0' and col!='PNL_1']])[:832]

In [14]:
X_train.shape

(832, 10)

In [15]:
scaler = MinMaxScaler(feature_range=(0, 1))
X_train = scaler.fit_transform(X_train)
X_train = X_train.reshape(X_train.shape[0],1,X_train.shape[1])
y_train = to_categorical(bt[:832],num_classes=4)

In [16]:
X_train.shape, y_train.shape

((832, 1, 10), (832, 4))

### red neuronal recurrente
para empezar probaremos unidades LSTM solo con cuatro días de entrenamiento y probando al quinto día

In [30]:
model = Sequential()

model.add(LSTM(32,input_shape=(X_train.shape[1],X_train.shape[2]),activation='tanh', return_sequences=True))
model.add(Dropout(0.5))
model.add(LSTM(64, activation='softmax'))
model.add(Dropout(0.5))
model.add(Dense(10))
model.add(Dense(4, activation='softmax'))

model.compile(loss='categorical_crossentropy', optimizer='rmsprop', metrics=['accuracy'])

In [31]:
def compute_class_weigth(y):
    u = np.unique(y)
    r = {}
    for i in range(len(u)):
        r[i] = sum(u[0]==y)/sum(u[i]==y)
        
    return r

In [32]:
print('label 0: ', sum(bt[:832]==0))
print('label 1: ', sum(bt[:832]==1))
print('label 2: ', sum(bt[:832]==2))
print('label 3: ', sum(bt[:832]==3))

label 0:  336
label 1:  375
label 2:  56
label 3:  65


In [33]:
cw = compute_class_weigth(bt[:832])
cw

{0: 1.0, 1: 0.89600000000000002, 2: 6.0, 3: 5.1692307692307695}

In [34]:
#model.fit(X_train, y_train, epochs=50, batch_size=1000)
#model.fit(X_train, y_train, epochs=2000, batch_size=200,class_weight={0:1, 1:0.8053, 2:2.275, 3:2.5277})
model.fit(X_train, y_train, epochs=2000, batch_size=200,class_weight=cw)
#model.fit(X_train, y_train, epochs=2000, batch_size=200,class_weight=cw)

Epoch 1/2000
832/832 [==============================] - 0s - loss: 2.2407 - acc: 0.2692     
Epoch 2/2000
832/832 [==============================] - 0s - loss: 2.2406 - acc: 0.2825     
Epoch 3/2000
832/832 [==============================] - 0s - loss: 2.2420 - acc: 0.2308     
Epoch 4/2000
832/832 [==============================] - 0s - loss: 2.2399 - acc: 0.2873     
Epoch 5/2000
832/832 [==============================] - 0s - loss: 2.2392 - acc: 0.2861     
Epoch 6/2000
832/832 [==============================] - 0s - loss: 2.2404 - acc: 0.3005     
Epoch 7/2000
832/832 [==============================] - 0s - loss: 2.2402 - acc: 0.2500     
Epoch 8/2000
832/832 [==============================] - 0s - loss: 2.2398 - acc: 0.3413     
Epoch 9/2000
832/832 [==============================] - 0s - loss: 2.2390 - acc: 0.2752     
Epoch 10/2000
832/832 [==============================] - 0s - loss: 2.2404 - acc: 0.2692     
Epoch 11/2000
832/832 [==============================] - 0s - loss: 2

832/832 [==============================] - 0s - loss: 2.2352 - acc: 0.2812     
Epoch 89/2000
832/832 [==============================] - 0s - loss: 2.2340 - acc: 0.2476     
Epoch 90/2000
832/832 [==============================] - 0s - loss: 2.2323 - acc: 0.2512     
Epoch 91/2000
832/832 [==============================] - 0s - loss: 2.2337 - acc: 0.2993     
Epoch 92/2000
832/832 [==============================] - 0s - loss: 2.2335 - acc: 0.2969     
Epoch 93/2000
832/832 [==============================] - 0s - loss: 2.2330 - acc: 0.2897     
Epoch 94/2000
832/832 [==============================] - 0s - loss: 2.2305 - acc: 0.3570     
Epoch 95/2000
832/832 [==============================] - 0s - loss: 2.2311 - acc: 0.3221     
Epoch 96/2000
832/832 [==============================] - 0s - loss: 2.2346 - acc: 0.2704     
Epoch 97/2000
832/832 [==============================] - 0s - loss: 2.2316 - acc: 0.2524     
Epoch 98/2000
832/832 [==============================] - 0s - loss: 2.2344

832/832 [==============================] - 0s - loss: 2.2121 - acc: 0.2849     
Epoch 175/2000
832/832 [==============================] - 0s - loss: 2.2179 - acc: 0.2752     
Epoch 176/2000
832/832 [==============================] - 0s - loss: 2.2219 - acc: 0.2716     
Epoch 177/2000
832/832 [==============================] - 0s - loss: 2.2178 - acc: 0.3053     
Epoch 178/2000
832/832 [==============================] - 0s - loss: 2.2172 - acc: 0.2668     
Epoch 179/2000
832/832 [==============================] - 0s - loss: 2.2179 - acc: 0.2897     
Epoch 180/2000
832/832 [==============================] - 0s - loss: 2.2110 - acc: 0.2969     
Epoch 181/2000
832/832 [==============================] - 0s - loss: 2.2153 - acc: 0.3113     
Epoch 182/2000
832/832 [==============================] - 0s - loss: 2.2251 - acc: 0.3101     
Epoch 183/2000
832/832 [==============================] - 0s - loss: 2.2218 - acc: 0.2776     
Epoch 184/2000
832/832 [==============================] - 0s - lo

832/832 [==============================] - 0s - loss: 2.2082 - acc: 0.3173     
Epoch 261/2000
832/832 [==============================] - 0s - loss: 2.2188 - acc: 0.3053     
Epoch 262/2000
832/832 [==============================] - 0s - loss: 2.2143 - acc: 0.3101     
Epoch 263/2000
832/832 [==============================] - 0s - loss: 2.2164 - acc: 0.3029     
Epoch 264/2000
832/832 [==============================] - 0s - loss: 2.2149 - acc: 0.3113     
Epoch 265/2000
832/832 [==============================] - 0s - loss: 2.2162 - acc: 0.3137     
Epoch 266/2000
832/832 [==============================] - 0s - loss: 2.2111 - acc: 0.3029     
Epoch 267/2000
832/832 [==============================] - 0s - loss: 2.2160 - acc: 0.2825     
Epoch 268/2000
832/832 [==============================] - 0s - loss: 2.2114 - acc: 0.3077     
Epoch 269/2000
832/832 [==============================] - 0s - loss: 2.2141 - acc: 0.2981     
Epoch 270/2000
832/832 [==============================] - 0s - lo

832/832 [==============================] - 0s - loss: 2.2131 - acc: 0.3053     
Epoch 347/2000
832/832 [==============================] - 0s - loss: 2.2155 - acc: 0.3209     
Epoch 348/2000
832/832 [==============================] - 0s - loss: 2.2049 - acc: 0.3113     
Epoch 349/2000
832/832 [==============================] - 0s - loss: 2.2040 - acc: 0.3113     
Epoch 350/2000
832/832 [==============================] - 0s - loss: 2.2046 - acc: 0.3053     
Epoch 351/2000
832/832 [==============================] - 0s - loss: 2.2025 - acc: 0.3185     
Epoch 352/2000
832/832 [==============================] - 0s - loss: 2.2032 - acc: 0.3281     
Epoch 353/2000
832/832 [==============================] - 0s - loss: 2.2067 - acc: 0.3317     
Epoch 354/2000
832/832 [==============================] - 0s - loss: 2.2123 - acc: 0.3221     
Epoch 355/2000
832/832 [==============================] - 0s - loss: 2.2099 - acc: 0.3221     
Epoch 356/2000
832/832 [==============================] - 0s - lo

...

832/832 [==============================] - 0s - loss: 2.2115 - acc: 0.3365     
Epoch 1630/2000
832/832 [==============================] - 0s - loss: 2.2071 - acc: 0.3438     
Epoch 1631/2000
832/832 [==============================] - 0s - loss: 2.2108 - acc: 0.3377     
Epoch 1632/2000
832/832 [==============================] - 0s - loss: 2.2025 - acc: 0.3437     
Epoch 1633/2000
832/832 [==============================] - 0s - loss: 2.2052 - acc: 0.3257     
Epoch 1634/2000
832/832 [==============================] - 0s - loss: 2.2083 - acc: 0.3113     
Epoch 1635/2000
832/832 [==============================] - 0s - loss: 2.2126 - acc: 0.3101     
Epoch 1636/2000
832/832 [==============================] - 0s - loss: 2.2164 - acc: 0.3293     
Epoch 1637/2000
832/832 [==============================] - 0s - loss: 2.2113 - acc: 0.3353     
Epoch 1638/2000
832/832 [==============================] - 0s - loss: 2.2046 - acc: 0.3305     
Epoch 1639/2000
832/832 [==============================]

832/832 [==============================] - 0s - loss: 2.2017 - acc: 0.3281     
Epoch 1715/2000
832/832 [==============================] - 0s - loss: 2.2021 - acc: 0.3413     
Epoch 1716/2000
832/832 [==============================] - 0s - loss: 2.1958 - acc: 0.3486     
Epoch 1717/2000
832/832 [==============================] - 0s - loss: 2.2027 - acc: 0.3558     
Epoch 1718/2000
832/832 [==============================] - 0s - loss: 2.2103 - acc: 0.3486     
Epoch 1719/2000
832/832 [==============================] - 0s - loss: 2.2056 - acc: 0.3365     
Epoch 1720/2000
832/832 [==============================] - 0s - loss: 2.2089 - acc: 0.3389     
Epoch 1721/2000
832/832 [==============================] - 0s - loss: 2.2074 - acc: 0.3401     
Epoch 1722/2000
832/832 [==============================] - 0s - loss: 2.2043 - acc: 0.3341     
Epoch 1723/2000
832/832 [==============================] - 0s - loss: 2.2013 - acc: 0.3161     
Epoch 1724/2000
832/832 [==============================]

832/832 [==============================] - 0s - loss: 2.2163 - acc: 0.3401     
Epoch 1800/2000
832/832 [==============================] - 0s - loss: 2.1959 - acc: 0.3522     
Epoch 1801/2000
832/832 [==============================] - 0s - loss: 2.2209 - acc: 0.3498     
Epoch 1802/2000
832/832 [==============================] - 0s - loss: 2.2071 - acc: 0.3437     
Epoch 1803/2000
832/832 [==============================] - 0s - loss: 2.2111 - acc: 0.3510     
Epoch 1804/2000
832/832 [==============================] - 0s - loss: 2.2056 - acc: 0.3450     
Epoch 1805/2000
832/832 [==============================] - 0s - loss: 2.2075 - acc: 0.3438     
Epoch 1806/2000
832/832 [==============================] - 0s - loss: 2.2046 - acc: 0.3522     
Epoch 1807/2000
832/832 [==============================] - 0s - loss: 2.2077 - acc: 0.3401     
Epoch 1808/2000
832/832 [==============================] - 0s - loss: 2.2114 - acc: 0.3305     
Epoch 1809/2000
832/832 [==============================]

832/832 [==============================] - 0s - loss: 2.1958 - acc: 0.2981     
Epoch 1885/2000
832/832 [==============================] - 0s - loss: 2.2037 - acc: 0.2993     
Epoch 1886/2000
832/832 [==============================] - 0s - loss: 2.2068 - acc: 0.3209     
Epoch 1887/2000
832/832 [==============================] - 0s - loss: 2.2058 - acc: 0.3510     
Epoch 1888/2000
832/832 [==============================] - 0s - loss: 2.2054 - acc: 0.3329     
Epoch 1889/2000
832/832 [==============================] - 0s - loss: 2.2107 - acc: 0.3185     
Epoch 1890/2000
832/832 [==============================] - 0s - loss: 2.2054 - acc: 0.3245     
Epoch 1891/2000
832/832 [==============================] - 0s - loss: 2.1970 - acc: 0.3101     
Epoch 1892/2000
832/832 [==============================] - 0s - loss: 2.2088 - acc: 0.3197     
Epoch 1893/2000
832/832 [==============================] - 0s - loss: 2.2138 - acc: 0.3317     
Epoch 1894/2000
832/832 [==============================]

832/832 [==============================] - 0s - loss: 2.2050 - acc: 0.2284     
Epoch 1970/2000
832/832 [==============================] - 0s - loss: 2.2088 - acc: 0.2380     
Epoch 1971/2000
832/832 [==============================] - 0s - loss: 2.2004 - acc: 0.2536     
Epoch 1972/2000
832/832 [==============================] - 0s - loss: 2.2049 - acc: 0.3041     
Epoch 1973/2000
832/832 [==============================] - 0s - loss: 2.2107 - acc: 0.2764     
Epoch 1974/2000
832/832 [==============================] - 0s - loss: 2.2095 - acc: 0.2969     
Epoch 1975/2000
832/832 [==============================] - 0s - loss: 2.1998 - acc: 0.2873     
Epoch 1976/2000
832/832 [==============================] - 0s - loss: 2.2042 - acc: 0.2957     
Epoch 1977/2000
832/832 [==============================] - 0s - loss: 2.2028 - acc: 0.2993     
Epoch 1978/2000
832/832 [==============================] - 0s - loss: 2.2120 - acc: 0.2764     
Epoch 1979/2000
832/832 [==============================]

In [35]:
X_test = np.array(X[[col for col in X.columns if col!='PNL_0' and col!='PNL_1']])[833:1113]

In [36]:
scaler = MinMaxScaler(feature_range=(0, 1))
X_test = scaler.fit_transform(X_test)
X_test = X_test.reshape(X_test.shape[0],1,X_test.shape[1])
y_test = to_categorical(bt[833:1113],num_classes=4)

In [37]:
predict = model.predict_classes(X_test)
np.unique(predict)

 32/280 [==>...........................] - ETA: 1s

array([0, 2, 3])

In [38]:
bt_test = bt[833:1113]

In [39]:
print('label 0: ', sum(bt_test==0))
print('label 1: ', sum(bt_test==1))
print('label 2: ', sum(bt_test==2))
print('label 3: ', sum(bt_test==3))

label 0:  124
label 1:  104
label 2:  29
label 3:  23


In [40]:
print('predict 0: ', sum(predict==0))
print('predict 1: ', sum(predict==1))
print('predict 2: ', sum(predict==2))
print('predict 3: ', sum(predict==3))

predict 0:  261
predict 1:  0
predict 2:  3
predict 3:  16


In [41]:
l_zero, l_one = [],[]
count_ones, count_zeros = 0,0
for i in range(len(predict)):
    if predict[i]==1:
        l_zero.append(count_zeros)
        count_zeros = 0
        count_ones += 1
    else:
        l_one.append(count_ones)
        count_zeros += 1
        count_ones = 0
    
    if i==len(predict)-1:
        l_one.append(count_ones)
        l_zero.append(count_zeros)

print('PNL accumulated: ',sum((predict==1)*X_test_PNL_1 + (predict==0)*X_test_PNL_0))
print('buy mes: ', sum(predict==1)+sum(predict==3))
print('sell mes: ',sum(predict==0)+sum(predict==2))
print('longest buy: ', max(l_one))
print('longest sell: ', max(l_zero))
print('correct target 1: ', np.mean((predict==1)*(bt_test==1)))
print('correct target 0: ', np.mean((predict==0)*(bt_test==0)))
print('correct target 2: ', np.mean((predict==2)*(bt_test==2)))
print('correct target 3: ', np.mean((predict==3)*(bt_test==3)))
print('percision total: ', np.mean(predict==bt_test))

PNL accumulated:  -0.00318
buy mes:  16
sell mes:  264
longest buy:  0
longest sell:  280
correct target 1:  0.0
correct target 0:  0.421428571429
correct target 2:  0.0
correct target 3:  0.0
percision total:  0.421428571429


#### Conlcusiones
cabe anotar que el error del gradiente disminuye demasiado lento, de hecho se utilizaron 5000 epochs y su disminución del error fue poca, mas sin embargo al pesar las etiquetas la red se comporta de una mejor forma, inclusive haciendo que se genere una ganancia de 0.002121 USD en ese día de comercio, habrá que probar como se comporta en todo un mes.

#### Nuevas Pruebas
Ahora probaremos generando una RNN la cual entrenaremos con datos de cuatro días para probarla en el quinto dia, y se va corriendo de a un día consecutivo.

In [42]:
# %load ../../code/EUtilities.py

In [43]:
def compute_class_weigth(y):
    u = np.unique(y)
    r = {}
    for i in range(len(u)):
        r[i] = sum(u[0]==y)/sum(u[i]==y)
        
    return r

def step_validationRNN(model, X, y, cv, n_epochs, n_batch_size, pnl_0, pnl_1,bt):
    '''
    Recibe un modelo keras,X,y, & un generador cv con el cual hace la validación
    dependiendo que la configuración que este tenga
    '''
    import numpy as np
    result = []
    for index in cv:
        cw = compute_class_weigth(bt[index[0]])
        model.fit(X[index[0]], y[index[0]],epochs=n_epochs, batch_size=n_batch_size,class_weight=cw)
        predict = model.predict_classes(X[index[1]])
        
        #result.append(sum((predict==1)*pnl_1[index[1]] + (predict==0)*pnl_0[index[1]]))
        
        r = sum((predict==1)*pnl_1[index[1]] + (predict==0)*pnl_0[index[1]])
        sell = sum(predict==0)
        buy = sum(predict==1)
        #percent_0 = np.mean(y==pre)*100
        percent_1 = np.mean((predict==1)*(bt[index[1]]==1)) # si sube y gano
        percent_0 = np.mean((predict==0)*(bt[index[1]]==0)) # si baja y gano
        percent_3 = np.mean((predict==3)*(bt[index[1]]==3)) # si sube y pierdo
        percent_2 = np.mean((predict==2)*(bt[index[1]]==2)) # si baja y pierdo
        
        count_ones, count_zeros = 0,0
        l_one, l_zero = [],[]
        for i in predict:
            if i==1:
                l_zero.append(count_zeros)
                count_zeros = 0
                count_ones += 1
            else:
                l_one.append(count_ones)
                count_zeros += 1
                count_ones = 0
        l_zero.append(count_zeros)
        l_one.append(count_ones)
        
        if index[0][0]==0:
            result = np.array([[r,buy,sell,max(l_one),max(l_zero),percent_1,percent_0,percent_3,percent_2]])
        else:
            result = np.concatenate((result,np.array([[r,buy,sell,max(l_one),max(l_zero),percent_1,percent_0,percent_3,percent_2]])),axis=0)
        
    return result

In [310]:
model = Sequential()

model.add(LSTM(16,input_shape=(X_rnn.shape[1],X_rnn.shape[2]),activation='tanh'))
model.add(Dropout(0.5))
model.add(Dense(4, activation='softmax'))

model.compile(loss='categorical_crossentropy', optimizer='rmsprop', metrics=['accuracy'])

In [44]:
PNL_0 = X.PNL_0
PNL_1 = X.PNL_1

X_rnn = np.array(X[[col for col in X.columns if col!='PNL_0' and col!='PNL_1']])

scaler = MinMaxScaler(feature_range=(0, 1))
X_rnn = scaler.fit_transform(X_rnn)
X_rnn = X_rnn.reshape(X_rnn.shape[0],1,X_rnn.shape[1])
y_rnn = to_categorical(bt,num_classes=4)

X_rnn.shape, y_rnn.shape

((6232, 1, 10), (6232, 4))

In [45]:
cw = compute_class_weigth(bt)
cw

{0: 1.0, 1: 0.97957695113056165, 2: 6.7149999999999999, 3: 6.6485148514851486}

In [46]:
from time import time

In [47]:
t_i = time()
r = step_validationRNN(model, X_rnn, y_rnn,EU.v_split(X,4,1,1),2000,200,PNL_0,PNL_1,bt)
t_f = time()

Epoch 1/2000
1122/1122 [==============================] - 0s - loss: 2.2814 - acc: 0.2745     
Epoch 2/2000
1122/1122 [==============================] - 0s - loss: 2.2828 - acc: 0.2799     
Epoch 3/2000
1122/1122 [==============================] - 0s - loss: 2.2864 - acc: 0.2380     
Epoch 4/2000
1122/1122 [==============================] - 0s - loss: 2.2812 - acc: 0.2228     
Epoch 5/2000
1122/1122 [==============================] - 0s - loss: 2.2828 - acc: 0.2317     
Epoch 6/2000
1122/1122 [==============================] - 0s - loss: 2.2896 - acc: 0.2611     
Epoch 7/2000
1122/1122 [==============================] - 0s - loss: 2.2873 - acc: 0.2389     
Epoch 8/2000
1122/1122 [==============================] - 0s - loss: 2.2796 - acc: 0.2638     
Epoch 9/2000
1122/1122 [==============================] - 0s - loss: 2.2854 - acc: 0.2406     
Epoch 10/2000
1122/1122 [==============================] - 0s - loss: 2.2970 - acc: 0.2175     
Epoch 11/2000
1122/1122 [========================

1122/1122 [==============================] - 0s - loss: 2.2865 - acc: 0.2531     
Epoch 87/2000
1122/1122 [==============================] - 0s - loss: 2.2788 - acc: 0.2371     
Epoch 88/2000
1122/1122 [==============================] - 0s - loss: 2.2827 - acc: 0.2531     
Epoch 89/2000
1122/1122 [==============================] - 0s - loss: 2.2826 - acc: 0.2754     
Epoch 90/2000
1122/1122 [==============================] - 0s - loss: 2.2746 - acc: 0.2709     
Epoch 91/2000
1122/1122 [==============================] - 0s - loss: 2.2724 - acc: 0.2522     
Epoch 92/2000
1122/1122 [==============================] - 0s - loss: 2.2786 - acc: 0.2308     
Epoch 93/2000
1122/1122 [==============================] - 0s - loss: 2.2797 - acc: 0.2807     
Epoch 94/2000
1122/1122 [==============================] - 0s - loss: 2.2844 - acc: 0.2344     
Epoch 95/2000
1122/1122 [==============================] - 0s - loss: 2.2857 - acc: 0.2513     
Epoch 96/2000
1122/1122 [=============================

1122/1122 [==============================] - 0s - loss: 2.2791 - acc: 0.2424     
Epoch 171/2000
1122/1122 [==============================] - 0s - loss: 2.2768 - acc: 0.2442     
Epoch 172/2000
1122/1122 [==============================] - 0s - loss: 2.2854 - acc: 0.2460     
Epoch 173/2000
1122/1122 [==============================] - 0s - loss: 2.2825 - acc: 0.2531     
Epoch 174/2000
1122/1122 [==============================] - 0s - loss: 2.2818 - acc: 0.2487     
Epoch 175/2000
1122/1122 [==============================] - 0s - loss: 2.2876 - acc: 0.2469     
Epoch 176/2000
1122/1122 [==============================] - 0s - loss: 2.2852 - acc: 0.3146     
Epoch 177/2000
1122/1122 [==============================] - 0s - loss: 2.2802 - acc: 0.2433     
Epoch 178/2000
1122/1122 [==============================] - 0s - loss: 2.2744 - acc: 0.2291     
Epoch 179/2000
1122/1122 [==============================] - 0s - loss: 2.2853 - acc: 0.2451     
Epoch 180/2000
1122/1122 [===================

1122/1122 [==============================] - 0s - loss: 2.2674 - acc: 0.2389     
Epoch 255/2000
1122/1122 [==============================] - 0s - loss: 2.2690 - acc: 0.2014     
Epoch 256/2000
1122/1122 [==============================] - 0s - loss: 2.2790 - acc: 0.2148     
Epoch 257/2000
1122/1122 [==============================] - 0s - loss: 2.2775 - acc: 0.2344     
Epoch 258/2000
1122/1122 [==============================] - 0s - loss: 2.2783 - acc: 0.1845     
Epoch 259/2000
1122/1122 [==============================] - 0s - loss: 2.2792 - acc: 0.2148     
Epoch 260/2000
1122/1122 [==============================] - 0s - loss: 2.2759 - acc: 0.1595     
Epoch 261/2000
1122/1122 [==============================] - 0s - loss: 2.2771 - acc: 0.1872     
Epoch 262/2000
1122/1122 [==============================] - 0s - loss: 2.2786 - acc: 0.1827     
Epoch 263/2000
1122/1122 [==============================] - 0s - loss: 2.2854 - acc: 0.1480     
Epoch 264/2000
1122/1122 [===================

1122/1122 [==============================] - 0s - loss: 2.2780 - acc: 0.1506     
Epoch 339/2000
1122/1122 [==============================] - 0s - loss: 2.2780 - acc: 0.2121     
Epoch 340/2000
1122/1122 [==============================] - 0s - loss: 2.2750 - acc: 0.1988     
Epoch 341/2000
1122/1122 [==============================] - 0s - loss: 2.2723 - acc: 0.1301     
Epoch 342/2000
1122/1122 [==============================] - 0s - loss: 2.2793 - acc: 0.1809     
Epoch 343/2000
1122/1122 [==============================] - 0s - loss: 2.2799 - acc: 0.1898     
Epoch 344/2000
1122/1122 [==============================] - 0s - loss: 2.2717 - acc: 0.2451     
Epoch 345/2000
1122/1122 [==============================] - 0s - loss: 2.2759 - acc: 0.1881     
Epoch 346/2000
1122/1122 [==============================] - 0s - loss: 2.2777 - acc: 0.1631     
Epoch 347/2000
1122/1122 [==============================] - 0s - loss: 2.2796 - acc: 0.1640     
Epoch 348/2000
1122/1122 [===================

...

850/850 [==============================] - 0s - loss: 2.3450 - acc: 0.2435     
Epoch 1647/2000
850/850 [==============================] - 0s - loss: 2.3455 - acc: 0.2024     
Epoch 1648/2000
850/850 [==============================] - 0s - loss: 2.3503 - acc: 0.2200     
Epoch 1649/2000
850/850 [==============================] - 0s - loss: 2.3677 - acc: 0.2365     
Epoch 1650/2000
850/850 [==============================] - 0s - loss: 2.3462 - acc: 0.2376     
Epoch 1651/2000
850/850 [==============================] - 0s - loss: 2.3766 - acc: 0.2471     
Epoch 1652/2000
850/850 [==============================] - 0s - loss: 2.3834 - acc: 0.2000     
Epoch 1653/2000
850/850 [==============================] - 0s - loss: 2.3593 - acc: 0.1847     
Epoch 1654/2000
850/850 [==============================] - 0s - loss: 2.3511 - acc: 0.2435     
Epoch 1655/2000
850/850 [==============================] - 0s - loss: 2.3455 - acc: 0.2082     
Epoch 1656/2000
850/850 [==============================]

850/850 [==============================] - 0s - loss: 2.3517 - acc: 0.1988     
Epoch 1732/2000
850/850 [==============================] - 0s - loss: 2.3697 - acc: 0.2306     
Epoch 1733/2000
850/850 [==============================] - 0s - loss: 2.3684 - acc: 0.2035     
Epoch 1734/2000
850/850 [==============================] - 0s - loss: 2.3756 - acc: 0.1929     
Epoch 1735/2000
850/850 [==============================] - 0s - loss: 2.3524 - acc: 0.2435     
Epoch 1736/2000
850/850 [==============================] - 0s - loss: 2.3581 - acc: 0.2153     
Epoch 1737/2000
850/850 [==============================] - 0s - loss: 2.3655 - acc: 0.2388     
Epoch 1738/2000
850/850 [==============================] - 0s - loss: 2.3484 - acc: 0.2224     
Epoch 1739/2000
850/850 [==============================] - 0s - loss: 2.3495 - acc: 0.2071     
Epoch 1740/2000
850/850 [==============================] - 0s - loss: 2.3553 - acc: 0.2388     
Epoch 1741/2000
850/850 [==============================]

850/850 [==============================] - 0s - loss: 2.3743 - acc: 0.2612     
Epoch 1817/2000
850/850 [==============================] - 0s - loss: 2.3558 - acc: 0.2929     
Epoch 1818/2000
850/850 [==============================] - 0s - loss: 2.3414 - acc: 0.2471     
Epoch 1819/2000
850/850 [==============================] - 0s - loss: 2.3664 - acc: 0.2059     
Epoch 1820/2000
850/850 [==============================] - 0s - loss: 2.3595 - acc: 0.2047     
Epoch 1821/2000
850/850 [==============================] - 0s - loss: 2.3603 - acc: 0.2129     
Epoch 1822/2000
850/850 [==============================] - 0s - loss: 2.3595 - acc: 0.2459     
Epoch 1823/2000
850/850 [==============================] - 0s - loss: 2.3462 - acc: 0.2106     
Epoch 1824/2000
850/850 [==============================] - 0s - loss: 2.3566 - acc: 0.2106     
Epoch 1825/2000
850/850 [==============================] - 0s - loss: 2.3459 - acc: 0.2141     
Epoch 1826/2000
850/850 [==============================]

850/850 [==============================] - 0s - loss: 2.3443 - acc: 0.2741     
Epoch 1902/2000
850/850 [==============================] - 0s - loss: 2.3894 - acc: 0.2553     
Epoch 1903/2000
850/850 [==============================] - 0s - loss: 2.3590 - acc: 0.2506     
Epoch 1904/2000
850/850 [==============================] - 0s - loss: 2.3518 - acc: 0.2565     
Epoch 1905/2000
850/850 [==============================] - 0s - loss: 2.3478 - acc: 0.2365     
Epoch 1906/2000
850/850 [==============================] - 0s - loss: 2.3539 - acc: 0.2847     
Epoch 1907/2000
850/850 [==============================] - 0s - loss: 2.3582 - acc: 0.2635     
Epoch 1908/2000
850/850 [==============================] - 0s - loss: 2.3685 - acc: 0.2224     
Epoch 1909/2000
850/850 [==============================] - 0s - loss: 2.3482 - acc: 0.2565     
Epoch 1910/2000
850/850 [==============================] - 0s - loss: 2.3678 - acc: 0.2671     
Epoch 1911/2000
850/850 [==============================]

850/850 [==============================] - 0s - loss: 2.3450 - acc: 0.2353     
Epoch 1987/2000
850/850 [==============================] - 0s - loss: 2.3602 - acc: 0.2282     
Epoch 1988/2000
850/850 [==============================] - 0s - loss: 2.3576 - acc: 0.2376     
Epoch 1989/2000
850/850 [==============================] - 0s - loss: 2.3496 - acc: 0.2188     
Epoch 1990/2000
850/850 [==============================] - 0s - loss: 2.3714 - acc: 0.2212     
Epoch 1991/2000
850/850 [==============================] - 0s - loss: 2.3552 - acc: 0.2647     
Epoch 1992/2000
850/850 [==============================] - 0s - loss: 2.3614 - acc: 0.2694     
Epoch 1993/2000
850/850 [==============================] - 0s - loss: 2.3669 - acc: 0.2753     
Epoch 1994/2000
850/850 [==============================] - 0s - loss: 2.3499 - acc: 0.2471     
Epoch 1995/2000
850/850 [==============================] - 0s - loss: 2.3517 - acc: 0.2953     
Epoch 1996/2000
850/850 [==============================]

In [49]:
t_f-t_i

2532.1745312213898

In [50]:
2766.93/60

46.1155

In [51]:
np.mean(r[:,0])

-0.0053869565217396567

In [52]:
r = pd.DataFrame(r, columns=['PNL','buy','sell','longest_buy','longest_sell','accuracy 1','accuracy 0',
                      'accuracy 3','accuracy 2'])

In [53]:
r

PNL    buy   sell  longest_buy  longest_sell  accuracy 1  accuracy 0  \
0   0.00000    0.0    0.0          0.0           1.0    0.000000    0.000000   
1  -0.00426   30.0   27.0         20.0         177.0    0.043011    0.039427   
2  -0.01243  283.0    0.0        283.0           0.0    0.424028    0.000000   
3  -0.00947  281.0    0.0        281.0           0.0    0.380783    0.000000   
4  -0.00413  173.0   38.0        113.0         106.0    0.265957    0.067376   
5  -0.02439    0.0  256.0          0.0         280.0    0.000000    0.367857   
6  -0.00138    1.0    0.0          1.0           0.0    0.000000    0.000000   
7  -0.00515  280.0    0.0        280.0           0.0    0.435714    0.000000   
8   0.00000    0.0    0.0          0.0         282.0    0.000000    0.000000   
9  -0.01908  288.0    0.0        288.0           0.0    0.447917    0.000000   
10  0.00000    0.0    0.0          0.0         282.0    0.000000    0.000000   
11 -0.01388  283.0    0.0        283.0           0.0    0.406360    0.000000   
12  0.00000    0.0    0.0          0.0           1.0    0.000000    0.000000   
13 -0.01014    0.0  282.0          0.0         282.0    0.000000    0.453901   
14  0.00000    0.0    0.0          0.0         280.0    0.000000    0.000000   
15  0.00000    0.0    0.0          0.0         282.0    0.000000    0.000000   
16 -0.00549  244.0   42.0        188.0          15.0    0.381119    0.083916   
17 -0.01701    0.0  284.0          0.0         284.0    0.000000    0.433099   
18 -0.00172    1.0    0.0          1.0           0.0    0.000000    0.000000   
19 -0.00065    8.0    0.0          5.0         196.0    0.010676    0.000000   
20  0.00335    0.0   22.0          0.0         281.0    0.000000    0.046263   
21  0.00191   48.0  183.0          7.0         139.0    0.076655    0.299652   
22  0.00002    0.0    1.0          0.0          23.0    0.000000    0.043478   

    accuracy 3  accuracy 2  
0     0.000000    0.000000  
1     0.032258    0.025090  
2     0.000000    0.000000  
3     0.000000    0.000000  
4     0.000000    0.007092  
5     0.000000    0.014286  
6     0.000000    0.000000  
7     0.000000    0.000000  
8     0.000000    0.056738  
9     0.000000    0.000000  
10    0.046099    0.000000  
11    0.000000    0.000000  
12    0.000000    0.000000  
13    0.000000    0.000000  
14    0.000000    0.060714  
15    0.000000    0.039007  
16    0.000000    0.000000  
17    0.000000    0.000000  
18    0.000000    0.000000  
19    0.000000    0.049822  
20    0.067616    0.000000  
21    0.024390    0.000000  
22    0.304348    0.000000

In [54]:
compute_class_weigth(bt)

{0: 1.0, 1: 0.97957695113056165, 2: 6.7149999999999999, 3: 6.6485148514851486}

In [55]:
print('PNL mean: ',np.mean(r.iloc[:,0]))
print('buy mean: ',np.mean(r.iloc[:,1]))
print('sell mean: ',np.mean(r.iloc[:,2]))
print('l_buy mean: ',np.mean(r.iloc[:,3]))
print('l_sell mean: ',np.mean(r.iloc[:,4]))
print('accuracy_1 mean: ',np.mean(r.iloc[:,5]))
print('accuracy_0 mean: ',np.mean(r.iloc[:,6]))
print('accuracy_3 mean: ',np.mean(r.iloc[:,7]))
print('accuracy_2 mean: ',np.mean(r.iloc[:,8]))
print('accuracy total mean: ', np.mean(r.iloc[:,5])+np.mean(r.iloc[:,6])+np.mean(r.iloc[:,7])+np.mean(r.iloc[:,8]))

PNL mean:  -0.005386956521739657
buy mean:  83.47826086956522
sell mean:  49.34782608695652
l_buy mean:  76.08695652173913
l_sell mean:  126.56521739130434
accuracy_1 mean:  0.12487916750321418
accuracy_0 mean:  0.0797812222336626
accuracy_3 mean:  0.02063961233255025
accuracy_2 mean:  0.010989067357579594
accuracy total mean:  0.23628906942700661
